In [17]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from pandas.plotting import table
import datetime as dt 
# dt as time_series operation
%matplotlib inline
# for display dataframe
from IPython.display import display
from IPython.display import display_html
def display_side_by_side(*args):
    html_str=''
    for df in args:
        html_str+=df.to_html()
    display_html(html_str.replace('table','table style="display:inline"'),raw=True)
# ignore warning
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter(action='ignore', category=UserWarning)
warnings.simplefilter(action='ignore', category=RuntimeWarning)
# storage
from google.datalab import Context
import google.datalab.bigquery as bq
try:
  from StringIO import StringIO
except ImportError:
  from io import BytesIO as StringIO
# ML
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import log_loss
import xgboost as xgb

In [2]:
!pip install chartify

  Using cached https://files.pythonhosted.org/packages/f0/a5/4f5686ec47c99caeba41b3a57b4b68d40e1c577ef213484d67bf26df9b1d/chartify-2.5.0-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/8b/e9/5c47710fe383f0582da668302a80a6355fe15c2ce2dde89b50fe34acefa6/Pillow-5.4.1-cp35-cp35m-manylinux1_x86_64.whl
  Using cached https://files.pythonhosted.org/packages/83/df/0f5dd132200728a86190397e1ea87cd76244e42d39ec5e88efd25b2abd7e/jupyter-1.0.0-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/74/46/e81907704ab203206769dee1385dc77e1407576ff8f50a0681d0a6b541be/colour-0.1.5-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/2c/10/5ed4ece1869781c4420de7983fcb2f1bf6522a5d6f6bd0b634ce057f4984/selenium-3.8.0-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.org/packages/e0/7a/8aefbc0ed078dec7951ac9a06dcd1869243ecd7bcbce26fa47bf5e469a8f/qtconsole-4.4.3-py2.py3-none-any.whl
  Using cached https://files.pythonhosted.or

mltoolbox-datalab-image-classification 0.2 has requirement pillow==3.4.1, but you'll have pillow 5.4.1 which is incompatible.
ipython 6.5.0 has requirement prompt-toolkit<2.0.0,>=1.0.15, but you'll have prompt-toolkit 2.0.9 which is incompatible.
  Found existing installation: Pillow 3.4.1
    Uninstalling Pillow-3.4.1:
      Successfully uninstalled Pillow-3.4.1
  Found existing installation: prompt-toolkit 1.0.15
    Uninstalling prompt-toolkit-1.0.15:
      Successfully uninstalled prompt-toolkit-1.0.15


In [3]:
import chartify

In [4]:
!pip install lime

In [5]:
import lime
import lime.lime_tabular
np.random.seed(1)

# Model Predction

In [5]:
X_val = pd.read_csv('X_val.csv')
Y_val = pd.read_csv('Y_val.csv')
X_train = pd.read_csv('X_train.csv')
Y_train = pd.read_csv('Y_train.csv')

In [6]:
# model
xgb_watchlist = [(X_train, Y_train), (X_val, Y_val)]
model = xgb.XGBClassifier(learning_rate=0.08, max_depth=4,n_estimators=300,\
                 subsample=0.5, seed=2,missing=-1)
model.fit(X_train, Y_train,eval_set=xgb_watchlist,eval_metric='logloss',
            early_stopping_rounds=20,verbose=70)
# caculating E_val

model_probs = model.predict_proba(X_val)
    # [:,1] to show the prob to is_churn = 1
model_val_score = log_loss(Y_val,model_probs[:,1])
print(model_val_score)

[0]	validation_0-logloss:0.627331	validation_1-logloss:0.627325
Multiple eval metrics have been passed: 'validation_1-logloss' will be used for early stopping.

Will train until validation_1-logloss hasn't improved in 20 rounds.
[70]	validation_0-logloss:0.133955	validation_1-logloss:0.132867
[140]	validation_0-logloss:0.133009	validation_1-logloss:0.132214
Stopping. Best iteration:
[175]	validation_0-logloss:0.132772	validation_1-logloss:0.132154

0.13215561108235704


# Model Prediction (Lift Chart)

In [8]:
## data
X_val['model_pred'] = model_probs[:,1]
X_val['is_churn'] = Y_val
# give 'quantile
# if we give q=50 , w'll get duplicated boundarys which make error
X_val['model_pred_quantile'] = pd.qcut(X_val['model_pred'],
       q=20, duplicates='drop',
      labels=[str(i-5) + '-' +  str(i) + '%' for i in range(100,0,-5)])
# mean churn rate
mean_churn = X_val['is_churn'].mean()*100
# aggregation
agg_data = X_val.groupby(by=['model_pred_quantile'])['is_churn'].mean().reset_index()
agg_data['is_churn'] = round(agg_data['is_churn'],2)*100
agg_data['model_pred_quantile'] = agg_data['model_pred_quantile'].astype('object')
agg_data['lift'] = round(agg_data['is_churn'] / mean_churn,2)
# for plots
agg_data_for_plot = agg_data.sort_values(by=['is_churn'],ascending=False)[:10]

In [25]:
ch = chartify.Chart(x_axis_type='categorical',
                    second_y_axis=True,
                    blank_labels=True)
ch.set_title("Model Prediction vs Churn Probability")
ch.set_subtitle("")
ch.plot.bar(
   data_frame=agg_data_for_plot,
   categorical_columns='model_pred_quantile',
   numeric_column='is_churn')
# churn rate
ch.plot.text(
        data_frame=agg_data_for_plot,
        categorical_columns='model_pred_quantile',
        numeric_column='is_churn',
        text_column='is_churn')
# lifts
# ch.plot.text(
#         data_frame=agg_data_for_plot,
#         categorical_columns='model_pred_quantile',
#         numeric_column='is_churn',
#         text_column='lift',
#         text_color='white',
#         y_offset=22)
ch.second_axis.axes.set_yaxis_label('Lift')
ch.second_axis.plot.text(
        data_frame=agg_data_for_plot,
        categorical_columns='model_pred_quantile',
        numeric_column='is_churn',
        text_column='lift',
        text_color='white',
        y_offset=22)
ch.callout.line(mean_churn,line_dash='dashed')
ch.axes.hide_yaxis()
ch.second_axis.axes.hide_yaxis()
ch.axes.set_yaxis_label('Churn rate(%)')
ch.axes.set_xaxis_label('Model Predction Quantitle')
ch.show()

## Model Explainability (Global)
* Permutation importance

## Model Explainability (Local) 

In [7]:
X_val = pd.read_csv('X_val.csv')
Y_val = pd.read_csv('Y_val.csv')
X_train = pd.read_csv('X_train.csv')
Y_train = pd.read_csv('Y_train.csv')

In [53]:
# model
xgb_watchlist = [(X_train.values, Y_train.values), (X_val.values, Y_val.values)]
model = xgb.XGBClassifier(learning_rate=0.08, max_depth=4,n_estimators=300,\
                 subsample=0.5, seed=2,missing=-1)
model.fit(X_train.values, Y_train.values,eval_set=xgb_watchlist,eval_metric='logloss',
            early_stopping_rounds=20,verbose=70)
# caculating E_val

model_probs = model.predict_proba(X_val.values)
    # [:,1] to show the prob to is_churn = 1
model_val_score = log_loss(Y_val.values,model_probs[:,1])
print(model_val_score)

[0]	validation_0-logloss:0.627331	validation_1-logloss:0.627325
Multiple eval metrics have been passed: 'validation_1-logloss' will be used for early stopping.

Will train until validation_1-logloss hasn't improved in 20 rounds.
[70]	validation_0-logloss:0.133955	validation_1-logloss:0.132867
[140]	validation_0-logloss:0.133009	validation_1-logloss:0.132214
Stopping. Best iteration:
[175]	validation_0-logloss:0.132772	validation_1-logloss:0.132154

0.13215561108235704


In [49]:
print(X_train.columns.tolist())
feature_list = ['6m_day_lis','6m_satis','reg_via','age_under_26','LL_churn','client_level','LA_renew','1m_day_listen']

['six_month_day_listen', 'six_month_satis', 'registered_via', 'age_under_26', 'last_last_churn', 'client_level_code', 'last_auto_renew', 'one_month_day_listen']


In [57]:
explainer = lime.lime_tabular.LimeTabularExplainer(X_train.values, 
                                                   feature_names=feature_list,
                                                   verbose=True,
                                                   class_names=['NOT_Churn','Churn'], discretize_continuous=False)

In [69]:
print('churn lables: ',(Y_val[Y_val['is_churn'] == 1.0].index.values))
print('NOT churn lables: ',(Y_val[Y_val['is_churn'] == 0.0].index.values))

churn lables:  [    39     61     79 ... 177268 177284 177292]
NOT churn lables:  [     0      1      2 ... 177297 177298 177299]


In [90]:
i = 152
print('actial label: ',Y_val.iloc[i].values[0])
exp = explainer.explain_instance(X_val.values[i], model.predict_proba,num_features=10)
exp.show_in_notebook()

actial label:  1.0
Intercept 0.04291759426982301
Prediction_local [0.34634979]
Right: 0.47242707


In [92]:
i = 176803
print('actial label: ',Y_val.iloc[i].values[0])
exp = explainer.explain_instance(X_val.values[i], model.predict_proba,num_features=10)
exp.show_in_notebook()

actial label:  1.0
Intercept 0.0523464257965453
Prediction_local [0.32728347]
Right: 0.31025177


In [93]:
i = 5
print('actial label: ',Y_val.iloc[i].values[0])
exp = explainer.explain_instance(X_val.values[i], model.predict_proba, num_features=10)
exp.show_in_notebook()

actial label:  0.0
Intercept 0.06095111908691495
Prediction_local [0.01977341]
Right: 0.009766622


In [94]:
i = 42
print('actial label: ',Y_val.iloc[i].values[0])
exp = explainer.explain_instance(X_val.values[i], model.predict_proba, num_features=10)
exp.show_in_notebook()

actial label:  0.0
Intercept 0.060821114474204775
Prediction_local [0.06852398]
Right: 0.015355765


## Example